In [1]:
import pandas as pd 

In [2]:
data_full=pd.read_csv('./results.csv')
data_full= data_full.drop(columns=['Unnamed: 0','Unnamed: 0.1'])
data_full.head(5)

semantic  correct_relationships  Success_Rate    model            CF  \
0       1.0                    1.0           1.0  forest0  FeatureTweak   
1       1.0                    0.0           NaN  forest0  FeatureTweak   
2       1.0                    1.0           NaN  forest0  FeatureTweak   
3       1.0                    0.0           NaN  forest0  FeatureTweak   
4       1.0                    1.0           NaN  forest0  FeatureTweak   

  dataset  
0  credit  
1  credit  
2  credit  
3  credit  
4  credit

In [3]:
#Delete Unncessary Data
data_full=data_full[data_full!='forest']
data_full=data_full[data_full!='linear']
data_full=data_full[data_full!='MLP']
#data_full=data_full[data_full!='do_calculus']
data_full['CF'] =  data_full['CF'].replace('FeatureTweak','FT')
data_full['CF'] =  data_full['CF'].replace('causal_recourse','CR')
data_full['CF'] =  data_full['CF'].replace('do_calculus','CR-A')
data_full['CF'] =  data_full['CF'].replace('actionable_recourse','AR')
data_full['CF'] =  data_full['CF'].replace('wachter','W-CF')
data_full['CF'] =  data_full['CF'].replace('growingspheres','GS')

In [4]:
#import plotly.graph_objects as go
#import numpy as np
#from plotly.subplots import make_subplots
# First Draft Comparing different Models
#df= data_full

#data= df
#i=1
#fig = make_subplots(rows=len(np.unique(data['dataset'])), cols=1)#fig = go.Figure()
#for a in np.unique(data['dataset']):
#    d= data[data['dataset']==a].sort_values('CF')
#    fig.add_trace(go.Box(x=d["CF"], y=d["semantic"], name='semantic',fillcolor='#D3D3D3', line={'color':'black'},boxmean='sd'),row=i, col=1 )
#    fig.add_trace(go.Box(x=d["CF"], y=d["correct_relationships"],name='relationship',fillcolor='#2F4F4F',line={'color':'black'},boxmean='sd'),row=i, col=1)
#    fig.update_xaxes(title_text=f"{a}", row=i, col=1)#tickangle=30)
#    i=i+1
#fig.update_traces(width=0.5)

#fig.update_layout(
#    yaxis_title='metric',
#   boxmode='group', # group together boxes of the different traces for each value of x
#        autosize=False,
#    width=1000,
#    height=1500,
#)
#fig.update_traces(width=0.5)
#fig.update_layout(boxgroupgap=0.5, boxgap=0.1)
#fig.show()

In [5]:
import numpy as np
print(data_full['CF'])

0          FT
1          FT
2          FT
3          FT
4          FT
         ... 
12274    W-CF
12275    W-CF
12276    W-CF
12277    W-CF
12278    W-CF
Name: CF, Length: 12279, dtype: object


In [6]:
#Same Plot But Item wise : 
#TODO Apply some restictions / Make nicer ? 
import plotly.graph_objects as go
import numpy as np
np.random.seed(1)

#TODO ADD ANTOTHE COLUMN IDICATING TYPE https://community.plotly.com/t/multicategory-axis-type-example/26392
item = []
for ty in data_full['CF']:
    if ty in ['W-CF', 'GS']:
        item.append('Constraints')
    elif ty in ['CR','CR-A']:
        item.append('Causal')
    elif ty in ['cchvae','Clue','Cruds','AR']:
        item.append('Surrogate')
    elif ty in ['focus','FT']:
        item.append('Specific')
    else:
        item.append('')
data_full['item']=item
for a in np.unique(data_full['dataset']):
    print(a)
    df=data_full[data_full['dataset']==a].sort_values(['item', 'CF'])
    df=df[df['model']!='linear0']
    #df=df[df['model']!='MLP0']
    #df=df[df['model']!='MLP1']
    #print(df['model'])
    fig = go.Figure()
    fig.add_trace(go.Box(x=[df['item'],df["CF"]], y=df["semantic"], name='smo',fillcolor='#D3D3D3', line={'color':'black'},boxmean='sd') )
    fig.add_trace(go.Box(x=[df['item'],df["CF"]], y=df["correct_relationships"],name='smr', fillcolor='#2F4F4F',line={'color':'black'},boxmean='sd'))

    fig.update_layout(
        yaxis_title='metric',
        boxmode='group' # group together boxes of the different traces for each value of x
    )
    fig.update_layout(legend=dict(
    yanchor="top",
    y=0.99,
    xanchor="left",
    x=0.01,
    
),
margin=dict(l=0,r=0,b=0,t=0),
template= 'plotly_white'
)

    fig.write_image(f"Overall_{a}.svg")
    fig.write_image(f"Overall_{a}.png")
    fig.show()

credit


economic


sanity-3-lin


sanity-3-non-add


sanity-3-non-lin


# BELOW HERE TESTING / EXPERIMENTAL STUFF

## Plots for RQ 2

In [7]:
# Semantic Meaningfulness in Comparison to accuracy of classifier 
# Scatter Plot ? 
import os
import torch
from string import digits
import re
import sklearn
import numpy as np
from carla.data.catalog import CsvCatalog
import pandas as pd
model_name=['0']
accuracy=['0']
precision=['0']
recall=['0']
auc=['0']
df=pd.DataFrame([])

for name in os.listdir('./Model/'):
    #print(name.split('.')[0][-1].isdigit())
    #print(name)
    if name.split('.')[0][-1].isdigit() or name.startswith('Linear')or name.startswith('Forest'):
        full_name=name
        model=torch.load(f'./Model/{name}')
        name=name.split('_')[1]
        name=name.replace('.pth','')
        #print('FIRST',name)
        #print(name[:-1])
        if name[-1].isdigit():
            name=name[:-1]
        #print('Second',name)

        dataset = pd.read_csv(f'../data/{name}/{name}.csv')
        continuous_wachter = dataset.drop(columns=['label']).columns
        scaler='Identity'
        if name == 'economic':
            scaler='MinMax'

        dataset = CsvCatalog(file_path=f'../data/{name}/{name}.csv',
                     continuous=continuous_wachter,
                     categorical=[],
                     immutables=[],
                     target='label',
                     scaling_method=scaler)
        dataset=dataset._df_test
        data_x, data_y=dataset.drop(columns=['label']), dataset['label']
        data_pred= model.predict(data_x)
        model_name.append(full_name)
        print(data_pred.shape)
        print(data_y.shape)
        if len(data_pred.shape)>1:
            data_pred= np.argmax(data_pred, axis=1)

        accuracy.append(sklearn.metrics.accuracy_score(data_y,data_pred))
        precision.append(sklearn.metrics.precision_score(data_y,data_pred))
        recall.append(sklearn.metrics.recall_score(data_y,data_pred))
        auc.append(sklearn.metrics.roc_auc_score(data_y,data_pred))
df['model_name']=model_name
#df['accuracy']=accuracy
#df['precision']=precision
#df['recall']=recall
df['auc'] =auc
df=df.iloc[1:]
df

/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning:

Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.

/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning:

Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.

/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning:

Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.

/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:5

[INFO] Using Python-MIP package version 1.12.0 [model.py <module>]
(2500,)
(2500,)
(2500,)
(2500,)
(2500,)
(2500,)
(2500,)
(2500,)
(2500,)
(2500,)


/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/Linear_TORCH/model_linear.py:34: UserWarning:

Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.

/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/Linear_TORCH/model_linear.py:34: UserWarning:

Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.

/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/Linear_TORCH/model_linear.py:34: UserWarning:

Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.



(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)


/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/Linear_TORCH/model_linear.py:34: UserWarning:

Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.

/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/Linear_TORCH/model_linear.py:34: UserWarning:

Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.

/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/ANN_TORCH/model_ann.py:56: UserWarning:

Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.

/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/ANN_TORCH/model_ann.py:56: UserWarning:

Implicit dimension choice for softmax has been deprecated. Change the cal

(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)


/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/ANN_TORCH/model_ann.py:56: UserWarning:

Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.

/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/ANN_TORCH/model_ann.py:56: UserWarning:

Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.

/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/ANN_TORCH/model_ann.py:56: UserWarning:

Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.



model_name       auc
1             Forest_credit.pth  0.807559
2           Forest_economic.pth  0.797684
3       Forest_sanity-3-lin.pth    0.8064
4   Forest_sanity-3-non-add.pth  0.744878
5   Forest_sanity-3-non-lin.pth  0.968658
6             Linear_credit.pth  0.764165
7           Linear_economic.pth  0.820964
8       Linear_sanity-3-lin.pth  0.994916
9   Linear_sanity-3-non-add.pth   0.99814
10  Linear_sanity-3-non-lin.pth  0.997359
11              MLP_credit0.pth  0.677016
12            MLP_economic0.pth  0.818565
13        MLP_sanity-3-lin0.pth  0.995996
14    MLP_sanity-3-non-add0.pth  0.995788
15    MLP_sanity-3-non-lin0.pth  0.999577

In [8]:
# Delete First Row 
smo=[]
smr=[]
data=data_full
# Attach smo, smr 
m=[]
for name in df['model_name']:
    name=name.replace('.pth','')
    a=name.split('_')
    if a[0]=='Forest':
        d=data[data['model']=='forest']
        d=d[d['dataset']==a[1]]
        m.append('Forest')
    if a[0]=='Linear':
        d=data[data['model']=='linear']
        d=d[d['dataset']==a[1]]
        m.append('Linear')
    if a[0]=='MLP':
        if int(a[1][-1])==0:
            d=data[data['model']=='MLP0']
            d=d[d['dataset']==a[1][:-1]]
            m.append('MLP_0')
        if int(a[1][-1])==1:
            d=data[data['model']=='MLP1']
            d=d[d['dataset']==a[1][:-1]]
            m.append('MLP_1')
        if int(a[1][-1])==2:
            d=data[data['model']=='MLP2']
            d=d[d['dataset']==a[1][:-1]]
            m.append('MLP_2')

        #Average results 
    smo.append(np.mean(d['semantic']))
    smr.append(np.mean(d["correct_relationships"]))
df['smo']=smo
df['smr']=smr
df['m']=m

## Averaged Results 
It Can be ssen that in most cases higher AUC also leafs to higher smr / smo --> Naming outliers is probably inetersting ! Maybe do this appraoch wise ? 

In [9]:
import plotly.express as px

fig = px.scatter(df, x="smr", y="auc",color="m")
fig.show()

In [10]:
import plotly.express as px

fig = px.scatter(df, x="smo", y="auc",color="m")
fig.show()

### Approach Wise Averaged Results

In [11]:
# Delete First Row 
smo=[]
smr=[]
acc=[]
data=data_full
df_new=pd.DataFrame([])
# Attach smo, smr 
m=[]
approach=[]
for name in df['model_name']:
    name=name.replace('.pth','')
    a=name.split('_')
    if a[0]=='Forest':
        d=data[data['model']=='forest']
        d=d[d['dataset']==a[1]]
        for cf in np.unique(d['CF']):
            d_cf=d[d['CF']==cf]
            smo.append(np.mean(d_cf['semantic']))
            smr.append(np.mean(d_cf["correct_relationships"]))
            m.append('Forest')
            approach.append(cf)
            #print(name)
            #print(df[df['model_name']==name]['auc'])
            acc.append(df[df['model_name']==name+'.pth']['auc'].values[0])

    if a[0]=='Linear':
        d=data[data['model']=='linear']
        d=d[d['dataset']==a[1]]
        for cf in np.unique(d['CF']):
            d_cf=d[d['CF']==cf]
            smo.append(np.mean(d_cf['semantic']))
            smr.append(np.mean(d_cf["correct_relationships"]))
            m.append('Linear')
            approach.append(cf)
            #print(name)
            #print(df[df['model_name']==name]['auc'])
            acc.append(df[df['model_name']==name+'.pth']['auc'].values[0])
    if a[0]=='MLP':
        if int(a[1][-1])==0:
            d=data[data['model']=='MLP0']
            d=d[d['dataset']==a[1][:-1]]
            
            for cf in np.unique(d['CF']):
                d_cf=d[d['CF']==cf]
                smo.append(np.mean(d_cf['semantic']))
                smr.append(np.mean(d_cf["correct_relationships"]))
                m.append('MLP_0')
                approach.append(cf)
                #print(name)
                #print(df[df['model_name']==name]['auc'])
                acc.append(df[df['model_name']==name+'.pth']['auc'].values[0])
        if int(a[1][-1])==1:
            d=data[data['model']=='MLP1']
            d=d[d['dataset']==a[1][:-1]]
        
            for cf in np.unique(d['CF']):
                d_cf=d[d['CF']==cf]
                smo.append(np.mean(d_cf['semantic']))
                smr.append(np.mean(d_cf["correct_relationships"]))
                m.append('MLP_1')
                approach.append(cf)
                #print(name)
                #print(df[df['model_name']==name]['auc'])
                acc.append(df[df['model_name']==name+'.pth']['auc'].values[0])
        if int(a[1][-1])==2:
            d=data[data['model']=='MLP2']
            d=d[d['dataset']==a[1][:-1]]
    
            for cf in np.unique(d['CF']):
                d_cf=d[d['CF']==cf]
                smo.append(np.mean(d_cf['semantic']))
                smr.append(np.mean(d_cf["correct_relationships"]))
                m.append('MLP_2')
                approach.append(cf)
                #print(name)
                #print(df[df['model_name']==name]['auc'])
                acc.append(df[df['model_name']==name+'.pth']['auc'].values[0])

        #Average results 
    #smo.append(np.mean(d['semantic']))
    #smr.append(np.mean(d["correct_relationships"]))

df_new['smo']=smo
df_new['smr']=smr
df_new['m']=m
df_new['cf']=approach
df_new['auc']=acc

In [12]:
df_new

smo       smr      m      cf       auc
0   0.420485  0.436658  MLP_0      AR  0.677016
1   0.140260  0.145455  MLP_0    Clue  0.677016
2   0.154857  0.176000  MLP_0   Cruds  0.677016
3   0.425300  0.431843  MLP_0      GS  0.677016
4   0.171296  0.170635  MLP_0    W-CF  0.677016
5   0.425300  0.431843  MLP_0  cchvae  0.677016
6   0.090909  0.090909  MLP_0   Cruds  0.818565
7   0.091511  0.091511  MLP_0      GS  0.818565
8   0.090909  0.090909  MLP_0    W-CF  0.818565
9   0.098736  0.104756  MLP_0  cchvae  0.818565
10  0.428571  0.571429  MLP_0      AR  0.995996
11  0.672000  0.668000  MLP_0      CR  0.995996
12  0.680000  0.628000  MLP_0    CR-A  0.995996
13  0.176309  0.184573  MLP_0    Clue  0.995996
14  0.162963  0.170370  MLP_0   Cruds  0.995996
15  0.495868  0.504132  MLP_0      GS  0.995996
16  0.254351  0.283802  MLP_0    W-CF  0.995996
17  0.600000  0.592000  MLP_0  cchvae  0.995996
18  0.389333  0.389333  MLP_0      CR  0.995788
19  0.381333  0.377333  MLP_0    CR-A  0.995788
20  0.166667  0.166667  MLP_0    Clue  0.995788
21  0.166667  0.166667  MLP_0   Cruds  0.995788
22  0.331624  0.335043  MLP_0      GS  0.995788
23  0.171521  0.195793  MLP_0    W-CF  0.995788
24  0.406667  0.422667  MLP_0  cchvae  0.995788
25  0.333333  0.666667  MLP_0      AR  0.999577
26  0.696000  0.736000  MLP_0      CR  0.999577
27  0.836000  0.856000  MLP_0    CR-A  0.999577
28  0.166667  0.166667  MLP_0    Clue  0.999577
29  0.306902  0.334802  MLP_0   Cruds  0.999577
30  0.496124  0.503876  MLP_0      GS  0.999577
31  0.384181  0.399718  MLP_0    W-CF  0.999577
32  0.519380  0.565891  MLP_0  cchvae  0.999577

In [13]:
import plotly.express as px
#TODO Why are forest based measures missing?
##CCHVAE Performs well for goof performing Classifier
## Causal Recourse also dependeny to good performance
## For loe performing Classifier most approaches < 0.8 perform semantically not well 

## CLue Wachter ---

fig = px.scatter(df_new, x="smr", y="auc",color="cf",symbol="cf",trendline="ols")
fig.update_layout(
    autosize=False,
    width=800,
    height=500,
margin=dict(l=0,r=0,b=0,t=0),
template= 'plotly_white'
)
fig.write_image(f"AUCvsSMR.svg")
fig.write_image(f"AUCvsSM0.png")
fig.show()

In [14]:
import plotly.express as px

fig = px.scatter(df_new, x="smo", y="auc",color="cf",symbol="cf",trendline="ols")

fig.update_layout(
    autosize=False,
    width=800,
    height=500,
margin=dict(l=0,r=0,b=0,t=0),
template= 'plotly_white'
)
fig.write_image(f"AUCvsSM0.svg")
fig.write_image(f"AUCvsSM0.png")
fig.show()

### Influence Model Type




In [15]:
import plotly.graph_objects as go
import numpy as np
np.random.seed(1)

df=data_full.sort_values('model')
df['model'] =  df['model'].replace('forest0','Forest')
df['model'] =  df['model'].replace('linear0','linear')
df['model']=  df['model'].replace('MLP0','MLP_0')
df['model'] =  df['model'].replace('MLP1','MLP_1')
df['model'] =  df['model'].replace('MLP2','MLP_2')


fig = go.Figure()
fig.add_trace(go.Box(x=df["model"], y=df["semantic"], name='semantic',boxmean='sd') )
fig.add_trace(go.Box(x=df["model"], y=df["correct_relationships"],name='relationship',boxmean='sd'))

fig.update_layout(
    boxmode='group', # group together boxes of the different traces for each value of x
    template= 'plotly_white',
    margin=dict(l=0,r=0,b=0,t=0),
)
fig.write_image(f"SplitModel.svg")
fig.write_image(f"SplitModel.png")
fig.show()

## Q3 Connection between SMO and SMR

In [16]:
import plotly.express as px
fig = px.scatter(x=data_full['semantic'], y=data_full["correct_relationships"],trendline="ols")
fig.update_layout(
        yaxis_title='smo',
        xaxis_title='smr',
        template= 'plotly_white',
        margin=dict(l=0,r=0,b=0,t=0),
    )
fig.write_image(f"SMOvsSMR.svg")
fig.show()

## Random Plots

In [17]:
import plotly.graph_objects as go
import numpy as np
np.random.seed(1)

fig = go.Figure()
fig.add_trace(go.Box(x=df["dataset"], y=df["semantic"], name='semantic') )
fig.add_trace(go.Box(x=df["dataset"], y=df["correct_relationships"],name='relationship'))

fig.update_layout(
    yaxis_title='normalized moisture',
    boxmode='group' # group together boxes of the different traces for each value of x
)

fig.show()

In [18]:
import plotly.graph_objects as go
import numpy as np
np.random.seed(1)

fig = go.Figure()
fig.add_trace(go.Box(x=df["CF"], y=df["semantic"], name='semantic') )
fig.add_trace(go.Box(x=df["CF"], y=df["correct_relationships"],name='relationship'))

fig.update_layout(
    yaxis_title='metric',
    boxmode='group' # group together boxes of the different traces for each value of x
)

fig.show()

In [19]:
# Just show mean 
pd.read_csv('./summary.csv')


Unnamed: 0  Unnamed: 0.1    model           dataset                   CF  \
0            0             0  forest0            credit         FeatureTweak   
1            0             0  linear0            credit  actionable_recourse   
2            0             0  linear0            credit               cchvae   
3            0             0  linear0            credit                 Clue   
4            0             0  linear0            credit                Cruds   
..         ...           ...      ...               ...                  ...   
71           0             0     MLP0  sanity-3-non-lin                 Clue   
72           0             0     MLP0  sanity-3-non-lin                Cruds   
73           0             0     MLP0  sanity-3-non-lin          do_calculus   
74           0             0     MLP0  sanity-3-non-lin       growingspheres   
75           0             0     MLP0  sanity-3-non-lin              wachter   

    semantic_mean  semantic_std  relationship_mean  relationship_std  
0        0.797263      0.317454           0.778443          0.332984  
1        0.423963      0.428547           0.433180          0.428547  
2        0.434857      0.435798           0.432571          0.433194  
3        0.137931      0.142772           0.147783          0.142772  
4        0.144000      0.144557           0.142857          0.142857  
..            ...           ...                ...               ...  
71       0.166667      0.166667           0.166667          0.166667  
72       0.306902      0.319517           0.334802          0.333330  
73       0.836000      0.370276           0.856000          0.351090  
74       0.496124      0.499985           0.503876          0.499985  
75       0.384181      0.354224           0.399718          0.358932  

[76 rows x 9 columns]

In [20]:
import plotly.express as px
fig = px.scatter(x=df['semantic'], y=df["correct_relationships"])
fig.show()

# Splitted Up According to Model

In [21]:
'''Only Forest Data'''
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.graph_objects as go
import numpy as np
np.random.seed(1)
data= df[df['model']=='forest']
i=1
fig = make_subplots(rows=1, cols=len(np.unique(data['dataset'])))#fig = go.Figure()
for a in np.unique(data['dataset']):
    d= data[data['dataset']==a].sort_values('CF')
    fig.add_trace(go.Box(x=d["CF"], y=d["semantic"], name='semantic'),row=1, col=i )
    fig.add_trace(go.Box(x=d["CF"], y=d["correct_relationships"],name='relationship'),row=1, col=i )
    fig.update_xaxes(title_text=f"{a}", row=1, col=i)
    i=i+1
   

fig.update_layout(
    yaxis_title='metric',
    boxmode='group' # group together boxes of the different traces for each value of x
)

fig.show()

ValueError: 
The 'cols' argument to make_suplots must be an int greater than 0.
    Received value of type <class 'int'>: 0

In [ ]:
'''Only Linear Data'''

from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.graph_objects as go
import numpy as np
np.random.seed(1)
data= df[df['model']=='linear']
i=1
fig = make_subplots(rows=1, cols=len(np.unique(data['dataset'])))#fig = go.Figure()
for a in np.unique(data['dataset']):
    d= data[data['dataset']==a].sort_values('CF')
    fig.add_trace(go.Box(x=d["CF"], y=d["semantic"], name='semantic'),row=1, col=i )
    fig.add_trace(go.Box(x=d["CF"], y=d["correct_relationships"],name='relationship'),row=1, col=i )
    fig.update_xaxes(title_text=f"{a}", row=1, col=i)
    i=i+1
    

fig.update_layout(
    yaxis_title='metric',
    boxmode='group' # group together boxes of the different traces for each value of x
)

fig.show()

In [ ]:
'''MLP'''
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.graph_objects as go
import numpy as np
np.random.seed(1)
data= df[df['model']=='MLP0']
i=1
fig = make_subplots(rows=1, cols=len(np.unique(data['dataset'])))#fig = go.Figure()
for a in np.unique(data['dataset']):
    d= data[data['dataset']==a].sort_values('CF')
    fig.add_trace(go.Box(x=d["CF"], y=d["semantic"], name='semantic'),row=1, col=i )
    fig.add_trace(go.Box(x=d["CF"], y=d["correct_relationships"],name='relationship'),row=1, col=i )
    fig.update_xaxes(title_text=f"{a}", row=1, col=i)
    i=i+1
    

fig.update_layout(
    yaxis_title='metric',
    boxmode='group' # group together boxes of the different traces for each value of x
)

fig.show()

# Splitted Up According to DatasetType 

In [ ]:
#Credit 
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.graph_objects as go
import numpy as np
np.random.seed(1)
data= df[df['dataset']=='credit']
i=1
fig = make_subplots(rows=1, cols=len(np.unique(data['model'])))#fig = go.Figure()
for a in np.unique(data['model']):
    d= data[data['model']==a].sort_values('CF')
    fig.add_trace(go.Box(x=d["CF"], y=d["semantic"], name='semantic'),row=1, col=i )
    fig.add_trace(go.Box(x=d["CF"], y=d["correct_relationships"],name='relationship'),row=1, col=i )
    fig.update_xaxes(title_text=f"{a}", row=1, col=i)
    i=i+1
    

fig.update_layout(
    yaxis_title='metric',
    boxmode='group' # group together boxes of the different traces for each value of x
)

fig.show()

In [ ]:
#Credit 
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.graph_objects as go
import numpy as np
np.random.seed(1)
data= df[df['dataset']=='sanity-3-lin']
i=1
fig = make_subplots(rows=1, cols=len(np.unique(data['model'])))#fig = go.Figure()
for a in np.unique(data['model']):
    d= data[data['model']==a].sort_values('CF')
    fig.add_trace(go.Box(x=d["CF"], y=d["semantic"], name='semantic'),row=1, col=i )
    fig.add_trace(go.Box(x=d["CF"], y=d["correct_relationships"],name='relationship'),row=1, col=i )
    fig.update_xaxes(title_text=f"{a}", row=1, col=i)
    i=i+1
    

fig.update_layout(
    yaxis_title='metric',
    boxmode='group' # group together boxes of the different traces for each value of x
)

fig.show()

In [ ]:
#Credit 
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.graph_objects as go
import numpy as np
np.random.seed(1)
data= df[df['dataset']=='sanity-3-non-lin']
i=1
fig = make_subplots(rows=1, cols=len(np.unique(data['model'])))#fig = go.Figure()
for a in np.unique(data['model']):
    d= data[data['model']==a].sort_values('CF')
    fig.add_trace(go.Box(x=d["CF"], y=d["semantic"], name='semantic'),row=1, col=i )
    fig.add_trace(go.Box(x=d["CF"], y=d["correct_relationships"],name='relationship'),row=1, col=i )
    fig.update_xaxes(title_text=f"{a}", row=1, col=i)
    i=i+1
    

fig.update_layout(
    yaxis_title='metric',
    boxmode='group' # group together boxes of the different traces for each value of x
)

fig.show()

In [ ]:
#Credit 
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.graph_objects as go
import numpy as np
np.random.seed(1)
data= df[df['dataset']=='sanity-3-non-add']
i=1
fig = make_subplots(rows=1, cols=len(np.unique(data['model'])))#fig = go.Figure()
for a in np.unique(data['model']):
    d= data[data['model']==a].sort_values('CF')
    fig.add_trace(go.Box(x=d["CF"], y=d["semantic"], name='semantic'),row=1, col=i )
    fig.add_trace(go.Box(x=d["CF"], y=d["correct_relationships"],name='relationship'),row=1, col=i )
    fig.update_xaxes(title_text=f"{a}", row=1, col=i)
    i=i+1
    

fig.update_layout(
    yaxis_title='metric',
    boxmode='group' # group together boxes of the different traces for each value of x
)

fig.show()

In [ ]:
# First Draft Comparing different Models
df= data_full
np.random.seed(1)
data= df[df['dataset']=='sanity-3-non-lin']
i=1
fig = make_subplots(rows=1, cols=len(np.unique(data['model'])))#fig = go.Figure()
for a in np.unique(data['model']):
    d= data[data['model']==a].sort_values('CF')
    fig.add_trace(go.Box(x=d["CF"], y=d["semantic"], name='semantic'),row=1, col=i )
    fig.add_trace(go.Box(x=d["CF"], y=d["correct_relationships"],name='relationship'),row=1, col=i )
    fig.update_xaxes(title_text=f"{a}", row=1, col=i)
    i=i+1
    

fig.update_layout(
    yaxis_title='metric',
    boxmode='group' # group together boxes of the different traces for each value of x
)

fig.show()

# Metrics in Comparison to Classification Capeabilities

(2500,)
(2500,)
(2500,)
(2500,)
(2500,)
(2500,)
(2500,)
(2500,)
(2500,)
(2500,)


/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/Linear_TORCH/model_linear.py:34: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  output = self.softmax(output)
/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/Linear_TORCH/model_linear.py:34: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  output = self.softmax(output)
/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/Linear_TORCH/model_linear.py:34: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  output = self.softmax(output)
/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/Linear_TORCH/model

(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)


/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/ANN_TORCH/model_ann.py:56: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  x = self.softmax(x)
/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/ANN_TORCH/model_ann.py:56: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  x = self.softmax(x)
/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/ANN_TORCH/model_ann.py:56: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  x = self.softmax(x)
/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1221: UndefinedMetricWarning: Precision is ill-defin

(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)


/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/ANN_TORCH/model_ann.py:56: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  x = self.softmax(x)
/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/ANN_TORCH/model_ann.py:56: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  x = self.softmax(x)
/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/ANN_TO

(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)
(2500, 2)
(2500,)


/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/ANN_TORCH/model_ann.py:56: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  x = self.softmax(x)
/home/jacqueline/.local/share/virtualenvs/CARLA-7s4zdYsf/lib/python3.7/site-packages/carla/models/catalog/ANN_TORCH/model_ann.py:56: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  x = self.softmax(x)


model_name accuracy precision    recall       auc
0                             0        0         0         0         0
1             Forest_credit.pth    0.806  0.827386  0.782575  0.806459
2           Forest_economic.pth   0.8168  0.763636  0.826617  0.818054
3       Forest_sanity-3-lin.pth    0.804  0.822311  0.794457  0.804389
4   Forest_sanity-3-non-add.pth   0.8604  0.928571  0.489796  0.738457
5   Forest_sanity-3-non-lin.pth   0.9732  0.977797   0.96543  0.972822
6             Linear_credit.pth   0.7676  0.783461   0.73756  0.767504
7           Linear_economic.pth   0.3536  0.336943  0.479167  0.366732
8       Linear_sanity-3-lin.pth   0.9956  0.998424  0.992947  0.995656
9   Linear_sanity-3-non-add.pth        1         1         1         1
10  Linear_sanity-3-non-lin.pth   0.9984   0.99918  0.997543  0.998381
11              MLP_credit0.pth   0.5128    0.5128         1       0.5
12              MLP_credit1.pth   0.6556  0.677305  0.605868  0.656042
13              MLP_credit2.pth   0.6808  0.703454  0.651835  0.681537
14            MLP_economic0.pth   0.5644         0         0       0.5
15            MLP_economic1.pth   0.8132  0.782004  0.784186  0.809637
16            MLP_economic2.pth    0.798  0.755773  0.787234  0.796718
17        MLP_sanity-3-lin0.pth   0.4712         0         0       0.5
18        MLP_sanity-3-lin1.pth    0.976  0.977695  0.977695  0.975861
19        MLP_sanity-3-lin2.pth   0.9904  0.986154  0.995342  0.990245
20    MLP_sanity-3-non-add0.pth   0.7324         0         0       0.5
21    MLP_sanity-3-non-add1.pth   0.7396         0         0       0.5
22    MLP_sanity-3-non-add2.pth   0.9956  0.989313  0.993865  0.995039
23    MLP_sanity-3-non-lin0.pth     0.47      0.47         1       0.5
24    MLP_sanity-3-non-lin1.pth   0.9988  0.997496         1  0.998851
25    MLP_sanity-3-non-lin2.pth   0.9992  0.998258         1  0.999261